In [24]:
import easyocr
import numpy as np
import cv2
import pandas as pd
import string
from collections import Counter
from nltk.corpus import stopwords
import pandas as pd
import cv2
#import pytesseract
from pytesseract import Output
import re
import pickle
import nltk
nltk.download('stopwords')
from nltk.corpus import stopwords
from transformers import BertTokenizer, BertModel
import torch

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

[nltk_data] Downloading package stopwords to /Users/alex/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [2]:
prepositions = [
                                "aboard", "about", "above", "across", "after", "against", "along", "amid", 
                                "among", "around", "as", "at", "before", "behind", "below", "beneath", 
                                "beside", "between", "beyond", "but", "by", "concerning", "considering", 
                                "despite", "down", "during", "except", "for", "from", "in", "inside", 
                                "into", "like", "near", "of", "off", "on", "onto", "out", "outside", 
                                "over", "past", "regarding", "round", "since", "through", "to", "toward", 
                                "under", "underneath", "until", "unto", "up", "upon", "with", "within", "without"
                              ]
exclude_words = ['de', 'en', 'al', 'alla', 'con','e','di','ai']
filter_words = stopwords.words('english') + prepositions #+ exclude_words

In [3]:
italian_menu_items = [
    'Panna Cotta', 'Cotoletta alla Milanese', 'Ravioli', 'Cannoli', 'Lasagna', 'Italian Cream Cake',
    'Osso Buco', 'Bruschetta', 'Focaccia', 'Antipasto', 'Ossobuco alla Milanese', 'Eggplant Parmigiana',
    'Italian Sausage', 'Prosciutto e Melone', 'Pasta e Fagioli', 'Cioppino', 'Tuscan Chicken',
    'Vitello Tonnato', 'Zuppa Toscana', 'Tiramisu', 'Risotto ai Frutti di Mare', 'Muffuletta',
    'Mozzarella in Carrozza', 'Spaghetti Carbonara', 'Biscotti', 'Ricotta Cheesecake', 'Pasta Fagioli',
    'Zeppole', 'Penne alla Vodka', 'Saltimbocca alla Romana', 'Spaghetti alla Puttanesca', 'Pollo alla Piccata',
    'Carpaccio', 'Caponata', 'Prosciutto', 'Spaghetti Bolognese', 'Lasagna alla Bolognese', 'Marsala',
    'Torta Caprese', 'Ziti', 'Burrata', 'Fettuccine Alfredo', 'Spaghetti and Meatballs', 'Vitello tonnato',
    'Pasta Pomodoro', 'Zabaglione', 'Porchetta', 'Baccala', 'Fusilli', 'Fritto Misto', 'Panzanella',
    'Orecchiette con le Cime di Rapa', 'Spaghetti alla Carbonara', 'Frutti di Mare', 'Pesto Genovese',
    'Stracciatella Soup', 'Chicken Parmigiana', 'Gelato', 'Pasta Primavera', 'Calzone', 'Sfogliatella',
    'Tiramisu Cake', 'Saltimbocca', 'Chicken Piccata', 'Gnocchi', 'Polenta', 'Limoncello',
    'Pollo alla Marsala', 'Minestrone', 'Baked Ziti', 'Grappa', 'Negroni', 'Cassata',
    'Minestrone Soup', 'Risotto alla Milanese', 'Risotto ai Funghi', 'Anisette', 'Espresso', 'Escarole Soup',
    'Bagna Cauda', 'Tortellini', 'Bistecca alla Fiorentina', 'Ribollita', 'Chicken Marsala',
    'Pesto alla Genovese', 'Pasta Aglio e Olio', 'Manicotti', 'Italian Wedding Soup', 'Arancini',
    'Amaretto', 'Caprese Salad', 'Pizza Margherita', 'Rigatoni', 'Affogato', 'Pappa al Pomodoro',
    'Frittata', 'Pizza Napoletana'
]


In [4]:
mexican_menu_items = [
    "Tacos al Pastor", "Chiles Rellenos", "Ceviche", "Tamales", "Pozole", "Guacamole", 
    "Enchiladas", "Chimichangas", "Churros", "Flan", "Empanadas", "Sopes", "Menudo", 
    "Mole Sauce", "Pico de Gallo", "Carnitas", "Carne Asada", "Fajitas", "Quesadillas", 
    "Nachos", "Tostadas", "Burritos", "Chorizo", "Tortas", "Pupusas", "Chilaquiles", 
    "Chiles en Nogada", "Horchata", "Carnitas", "Huevos Rancheros", "Carne en su Jugo", 
    "Enmolada", "Tlayuda", "Atole", "Tamarind Agua Fresca", "Bionicos", "Authentic Tacos Al Pastor",
    "Tamales De Puerco", "Mexican Corn On The Cob", "Mexican Sopes", "Churros", 
    "Authentic Mexican Torta", "Papas Rellenas", "Chef John's Horchata", "Birria De Chivo Estilo Jalisco",
    "Conchas", "Pozole In A Slow Cooker", "Avocado Paletas", "Creamy Caramel Flan", 
    "Classic Tres Leches Cake", "Fresas con Crema", "Conchas", "Mexican Cinnamon Cookies", 
    "Homemade Churros", "Strawberry Basil and Honey Paletas","Sopaipillas", "Mayan Chocolate Biscotti", 
    "Margarita Tres Leches Cake","Dulce de Leche Banana Cream Pie","Almond Coconut Flans", 
    "Pumpkin Cheesecake Empanadas","Cherry Biscochitos","Shortcut Tres Leches Cake","Arroz con Leche",
    "Sopaipilla Stars", "Pastelitos de Boda","Chilaquiles", "Mexican Egg Bake", 
    "Black Bean Huevos Rancheros", "Chorizo Breakfast Bowls","Migas", "Mexican Hash", "Carne Asada Breakfast Burrito", 
    "Papas Con Chorizo", "Microwave Longaniza Con Huevos", "Crispy Rolled Breakfast Burrito", "Migas Breakfast Tacos",
    "Michelada"
]

In [5]:
asian_menu_items = [
    'Halo-Halo', 'Bakso', 'Palak Paneer', 'Biryani', 'Tandoori Chicken','Nasi Goreng', 'Bao Buns', 'Tteokbokki', 
    'Rendang', 'Gỏi cuốn','Tempura', 'Hainanese Chicken', 'Satay', 'Hummus', 'Chicken Adobo',
    'Tonkatsu', 'Pani Puri', 'Laksa', 'Murtabak', 'Banh Mi','Baozi', 'Mango Sticky Rice', 'Soba', 'Beef Rendang', 
    'Onigiri', 'Naan', 'Char Siu', 'Egg Fried Rice', 'Goi Cuon', 'Udon','Hot Pot', 'Lechon', 'Chilli Crab', 
    'Chicken Rice', 'Mapo Tofu','Samosa', 'Som Tam', 'Massaman Curry', 'Roti Canai', 'Daal Makhani',
    'Butter Chicken', 'Soto Ayam', 'Tom Yum Soup', 'Sinigang', 'Galbi','Bak Kut Teh', 'Sweet and Sour Pork', 
    'Katsu Curry', 'Char Kway Teow', 'Bibimbap','Kung Pao Chicken', 'Peking Duck', 'Soondubu Jjigae', 'Curry Laksa', 
    'Kimchi','Kare-Kare', 'Cao Lau', 'Jiaozi', 'Yakitori', 'Xiao Long Bao','Spring Rolls', 'Tom Yum Goong', 
    'Century Egg', 'Pancit', 'Gimbap', 'Okonomiyaki', 'Pav Bhaji', 'Miso Soup', 'Shawarma', 'Nasi Lemak',
    'Rogan Josh', 'Vada Pav', 'Chicken Tikka Masala', 'Hainanese Chicken Rice', 'Takoyaki',
    'Dim Sum', 'Pho', 'Fish Head Curry', 'Green Curry', 'Balut','Japchae', 'Adobo', 'Falafel', 'Wonton Soup', 
    'Chole Bhature', 'Ramen', 'Pad Thai', 'Congee', 'Bun Cha', 'Bánh Xèo','Bulgogi', 'Sushi'
]


In [6]:
american_menu_items = [
    "Tater tots", "Burgers", "S'mores", "Biscuits", 
    "Pulled pork", "Shrimp and grits", "Key lime pie", "Lobster rolls", "Fried Green Tomatoes", 
    "lox bagel", "Cheeseburger", "Chocolate chip cookie", "Banana bread", "Cornbread", 
    "Cuban bread", "Frybread", "Texas toast", "American cheese","Avocado toast", "Indian Fry Bread", 
    "Turkey Shepherd's Pie","Steak and shrimp kabobs","Mashed Potatoes", "French Fries", "Cracker Jack", 
    "Congealed salads and casseroles", "Frozen orange juice", "Beef Wellington", "Smoothies", 
    "Lunchables", "Cupcakes", "Spare ribs", "Chicken wings", "Skewered beef", 
    "Fried wontons", "Fried shrimp", "Chicken fingers", "Crab Rangoon", "Gouda and Swiss cheeses", "Apple pie", 
    "Ground beef", "Sausage", "Cayenne pepper", "Hot Italian sausage", "Eggs","Rice",'Hamburger', 'Hot Dog', 
    'Chicken Nuggets', 'Pizza', 'Steak', 'Fried Chicken', 'BBQ Ribs', 'Lobster Roll', 'Clam Chowder', 'Buffalo Wings',
    'Philly Cheesesteak', 'Reuben Sandwich', 'Cobb Salad', 'Caesar Salad', 'Chicken Caesar Wrap', 'BLT Sandwich', 
    'Grilled Cheese Sandwich', 'Tuna Salad Sandwich', 'Egg Salad Sandwich', 'Chicken Alfredo', 'Spaghetti Bolognese',
    'Lasagna', 'Mac and Cheese', 'Fish and Chips', 'Shrimp Scampi', 'Crab Cakes', 'Lobster Bisque', 
    'Chicken Noodle Soup', 'Chicken and Waffles', 'Pancakes', 'Waffles', 'French Toast', 'Eggs Benedict', 
    'Bacon and Eggs', 'Sausage and Eggs', 'Omelette', 'Bagel and Cream Cheese', 
    'Donut', 'Cherry Pie', 'Pumpkin Pie', 'Cheesecake', 'Brownies', 'Ice Cream Sundae', 'Banana Split', 'Milkshake', 
    'Root Beer Float', 'Lemonade', 'Iced Tea', 'Hot Chocolate', 'Coffee', 'Espresso', 
    'Cappuccino', 'Latte', 'Mocha', 'Green Tea', 'Black Tea', 'Herbal Tea', 'Water', 'Orange Juice', 'Apple Juice', 
    'Grape Juice', 'Chocolate Milk', 'Strawberry Milkshake', 'Vanilla Milkshake', 'Chocolate Milkshake', 
    'Mimosa'
]

## Common Menu Words

In [7]:
df_dish = pd.read_csv('Dish.csv')

df_dish_mod = df_dish[df_dish.menus_appeared > 350].drop(columns = 'description')\
.sort_values(by = ['menus_appeared','times_appeared'], ascending = False).reset_index(drop=True)[:250]
dish_items = []
# for i in range(len(df_dish_mod)):
#     dish_items.append(df_dish_mod['name'][i])        
dish_items += american_menu_items
dish_items += italian_menu_items
dish_items += mexican_menu_items
dish_items += asian_menu_items
    
individual_words = [word.lower() for item in dish_items for word in item.split()]
word_counts = Counter(individual_words)
common_menu_words = [word for word, freq in word_counts.most_common(160)]#if word not in filter_words]
[common_menu_words.append(i) for i in ['feast','grill','grilled','skillet']]

[None, None, None]

In [12]:
with open('dish_items.pkl', 'wb') as f:
    pickle.dump(dish_items, f)

In [11]:
with open('common_menu_words.pkl', 'wb') as f:
    pickle.dump(common_menu_words, f)

In [8]:
common_menu_words

['chicken',
 'and',
 'alla',
 'soup',
 'pie',
 'spaghetti',
 'mexican',
 'fried',
 'chocolate',
 'rice',
 'sandwich',
 'salad',
 'cake',
 'pasta',
 'con',
 'de',
 'curry',
 'shrimp',
 'cheese',
 'juice',
 'beef',
 'sausage',
 'hot',
 'italian',
 'eggs',
 'egg',
 'cream',
 'milkshake',
 'tea',
 'breakfast',
 'lobster',
 'green',
 'banana',
 'bread',
 'toast',
 'crab',
 'pizza',
 'bolognese',
 'lasagna',
 'cheesecake',
 'milanese',
 'e',
 'risotto',
 'di',
 'marsala',
 'al',
 'tacos',
 'churros',
 'carne',
 'chorizo',
 'huevos',
 'tres',
 'leches',
 'pork',
 'rolls',
 'bagel',
 'avocado',
 'steak',
 'french',
 'orange',
 'ribs',
 'wings',
 'apple',
 'caesar',
 'alfredo',
 'fish',
 'waffles',
 'cherry',
 'pumpkin',
 'espresso',
 'black',
 'strawberry',
 'parmigiana',
 'prosciutto',
 'fagioli',
 'vitello',
 'tonnato',
 'tiramisu',
 'ai',
 'frutti',
 'mare',
 'in',
 'carbonara',
 'biscotti',
 'saltimbocca',
 'pollo',
 'piccata',
 'torta',
 'caprese',
 'ziti',
 'pomodoro',
 'pesto',
 'genove

In [2]:
# Load the list from the file
with open('dish_items.pkl', 'rb') as f:
    dish_items = pickle.load(f)

# Load the list from the file
with open('common_menu_words.pkl', 'rb') as f:
    common_menu_words = pickle.load(f)

In [21]:
start_menu = 1

stop_words = set(stopwords.words('english'))

prepositions = ['aboard', 'across', 'along', 'amid', 'among', 'around', 'behind', 'beneath', 'beside', 'beyond', \
                'concerning', 'considering', 'despite', 'except', 'inside', 'like', 'near', 'onto', 'outside', 'past',\
                'regarding', 'round', 'since', 'throughout', 'toward', 'underneath', 'unto', 'upon', 'within', 'without']

food_categories = ['gyros','sandwiches','toppings','sauces','orders','shareables','drinks', 'beverages', 'appetizers',\
                   'starters', 'salads', 'soups', 'entrees','entrées', 'main courses', 'desserts', 'sweets', 'sandwiches',\
                   'pizzas', 'burgers', 'pastas', 'seafood', 'steaks', 'vegetarian/vegan', 'sides', 'side dishes',\
                   'breakfast/brunch', "kids' menu", 'combos', 'platters', 'specials of the day', 'snacks', 'bar snacks',\
                   'sushi', 'japanese cuisine', 'dim sum', 'chinese cuisine', 'tacos', 'mexican cuisine', 'tapas',\
                   'spanish cuisine', 'mezze', 'mediterranean cuisine', 'bento', 'japanese lunch boxes', 'cuisines',\
                   'wraps/rolls', 'all you can eat', 'family style', 'shared dishes','sauce']

non_words = ['available',"choice","choices","add","oz","available","w",'served','side','additional','contains','allergy','.com',\
            'pizzeria','salads','soups','side items','appetizers','create','classics','your own','plates','extra']

non_words += food_categories

def count_uppercase_letters(text):
    return sum(1 for i in text if i.isupper())
def count_numerical_chars(text):
    return sum(1 for i in text if i.isdigit())
def count_punctuation(text):
    return sum(1 for i in text if i in string.punctuation and i not in [',', '.', '$',':'])
def count_common_menu_words(text):
    words = re.findall(r'\b[a-zA-Z]+\b', text)  # Extract words containing only alphabetical characters
    lowercase_words = [word.lower() for word in words]  # Convert all words to lowercase
    return sum(word in common_menu_words for word in lowercase_words)
def count_consecutive_periods(text):
    return len(re.findall(r'\.{2,}', text))
def non_words_count(text):
    words = re.findall(r'\b[a-zA-Z]+\b', text)  # Extract words containing only alphabetical characters
    lowercase_words = [word.lower() for word in words]  # Convert all words to lowercase
    return sum(lowercase_words.count(non_word) for non_word in non_words)
def stop_words_count(text):
    words = re.findall(r'\b[a-zA-Z]+\b', text)  # Extract words containing only alphabetical characters
    lowercase_words = [word.lower() for word in words]  # Convert all words to lowercase
    return sum(lowercase_words.count(stop_word) for stop_word in stop_words)
def prepositions_count(text):
    words = re.findall(r'\b[a-zA-Z]+\b', text)  # Extract words containing only alphabetical characters
    lowercase_words = [word.lower() for word in words]  # Convert all words to lowercase
    return sum(lowercase_words.count(preposition) for preposition in prepositions)

# Create a reader for English language
reader = easyocr.Reader(['en'])

files1 = ['menu_2p2.jp2','olive-garden-menu-6.jpeg','Red-Lobster-menu-1.jpeg','Red-Lobster-menu-2.jpeg',\
          'Red-Lobster-menu-5.jpeg','mexican-menu-1.jpeg','mexican-menu-2.jpeg','mexican-menu-3.jpeg',\
        'mexican-menu-4.jpeg','american-menu-1.jpeg','american-menu-2.jpeg','ivy-menu-1.jpeg','ivy-menu-2.jpeg']

files2 = ['topgolf_menu.jpeg','eggcited_menu.jpeg','steak-n-shake.jpeg','tgi_menu.jpeg','portillos_menu.jpeg',\
         'portillos_menu2.jpeg','meatheads_menu.jpeg','meatheads_menu2.jpeg','PitaPit_menu.jpeg','PitaPit_menu2.jpeg']

files = files1 + files2

for c,file in enumerate(files):    
    # Read the images using OpenCV
    image = cv2.imread(file)
    
    # Convert the image to RGB (OpenCV loads images in BGR format)
    image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
    
    # Get the dimensions of the image
    height_img, width_img, _ = image.shape
    area_img = width_img*height_img
    
    # Perform OCR on the image
    result = reader.readtext(image)

    # Prepare a list to store the data
    data = []

    # Loop through the results
    for (bbox, text, prob) in result:
        # unpack the bounding box
        (tl, tr, br, bl) = bbox
        tl = (int(tl[0]), int(tl[1]))
        tr = (int(tr[0]), int(tr[1]))
        br = (int(br[0]), int(br[1]))
        bl = (int(bl[0]), int(bl[1]))        
        
        # calculate the center coordinates
        center_x = int((tl[0] + tr[0] + br[0] + bl[0]) / 4)/(width_img)
        center_y = int((tl[1] + tr[1] + br[1] + bl[1]) / 4)/(height_img)

        # Compute the width and height of the bounding box
        width = np.sqrt((br[0]-bl[0])**2 + (br[1]-bl[1])**2)/(width_img)
        height = np.sqrt((tr[0]-br[0])**2 + (tr[1]-br[1])**2)/(height_img)

        # Compute the area of the bounding box
        area = (width * height)

        # Append the text, probability, bbox coordinates, width, height, and area to the data list
        data.append([text, center_x, center_y, width, height, area])

    # data_2 = [(entry[0], entry[6], entry[7], entry[8]) for entry in data]
    
    # Create a pandas DataFrame from the data
    df = pd.DataFrame(data, columns=["Text", "center_x" ,"center_y", "width", "height", "area"])

    # Select only 'Text' and 'Height' columns
    df.insert(0, 'Menu', c + start_menu)
    df = df[['Menu','Text', "center_x" ,"center_y", "width", 'height','area']]
#     df = df.astype({'width':'int'})
#     df = df.astype({'height':'int'})
#     df = df.astype({'area':'int'})
    df['uppercase'] = df['Text'].apply(count_uppercase_letters)

    df['Text'] = df['Text'].str.strip()
    # Add character count
    df['chars'] = df['Text'].apply(len)

    # Add word count
    df['words'] = df['Text'].apply(lambda x: len(x.split()))
    
    df['contains_dish'] = df['Text'].apply(lambda x: 1 if any(item in x for item in dish_items) else 0)

    df['common_words'] = df['Text'].apply(count_common_menu_words)    
    df['non_words'] = df['Text'].apply(lambda x: non_menu_words(x, non_words))

    df['periods'] = df['Text'].apply(lambda x: x.count('.'))
    df['period_btw_numbers'] = df['Text'].apply(lambda x: bool(re.search(r'\d\.\d', x))).astype(int)
    df['number_end'] = df['Text'].apply(lambda x: bool(re.search(r'\d$', x))).astype(int)
    df['numbers'] = df['Text'].apply(count_numerical_chars)
    df['commas'] = df['Text'].apply(lambda x: x.count(','))
    df['exclamation'] = df['Text'].apply(lambda x: x.count('!'))
    df['question'] = df['Text'].apply(lambda x: x.count('?'))
    df['colons'] = df['Text'].apply(lambda x: x.count(':'))
    df['underscores'] = df['Text'].apply(lambda x: x.count('_'))
    df['dollar'] = df['Text'].apply(lambda x: x.count('$'))
    df['punctuation'] = df['Text'].apply(count_punctuation)
    df['2_periods_cnt'] = df['Text'].apply(count_consecutive_periods)
    df['stop_words'] = df['Text'].apply(stop_words_count)
    df['prepositions'] = df['Text'].apply(prepositions_count)

    df['Item'] = np.zeros(len(df))
    df['Item'] = df['Item'].astype('int')
    if c > 0:
        dfs = pd.concat([dfs,df], ignore_index=True)
    else:
        dfs = df.copy()
dfs

Neither CUDA nor MPS are available - defaulting to CPU. Note: This module is much faster with a GPU.


Menu                                               Text  center_x  \
0        1                                              Soups  0.165238   
1        1                                                 16  0.091905   
2        1                                  Tom Yum Chicken*.  0.391429   
3        1                                               2.95  0.877143   
4        1                          spicy & sour w/ mushrooms  0.473810   
5        1                                              L5.95  0.858095   
6        1                               in lemon grass broth  0.407143   
7        1                                                 17  0.088095   
8        1                       Tom Yum Goong (shrimp) ,3.95  0.543810   
9        1                                              L6.95  0.855238   
10       1                                                 18  0.086190   
11       1                              Tom Kha Kai (chicken)  0.420952   
12       1                                               2.95  0.876190   
13       1                               creamy coconut milk;  0.399048   
14       1                                              L5.95  0.853810   
15       1                        lemon grass, straw mushroom  0.484286   
16       1                                          & galanga  0.296190   
17       1                                                 19  0.088095   
18       1                                     Soft Tofu Soup  0.341429   
19       1                                               2.95  0.874286   
20       1                                 ground pork & bean  0.395238   
21       1                                              L5.95  0.851905   
22       1                       thread noodles w/ vegetables  0.488571   
23       1                                       Noodle Soups  0.299048   
24       1                                                 20  0.076667   
25       1                                   Rice Noodle Soup  0.377619   
26       1                                               6.95  0.863810   
27       1               rice noodle w/ bean sprouts, choice]  0.566190   
28       1                           of chicken, beef,or pork  0.466190   
29       1                                                 21  0.070952   
30       1                                      Bamee/ Wonton  0.352857   
31       1                                               6.95  0.859048   
32       1                        egg noodle or wonton w/ BBQ  0.530000   
33       1                     pork,bean sprouts, green onion  0.527619   
34       1                                         & cilantro  0.305238   
35       1                                                 22  0.076667   
36       1                                   Tom Yum Noodle*_  0.367619   
37       1                                               7.25  0.848571   
38       1                       spicy rice or egg noodles w/  0.498571   
39       1                      groundpork; bean sprouts,fish  0.519524   
40       1                             balls & crushedpeanuts  0.450000   
41       1                                                 23  0.070000   
42       1                                       Red or Green  0.312857   
43       1                                               7.95  0.835238   
44       1                                      Curry Noodle*  0.350476   
45       2                                           Ogander/  0.164062   
46       2                          Create a Samplet Italiane  0.758854   
47       2                                          Antipasti  0.422917   
48       2                      Choose from: caramel, stuffed  0.761458   
49       2                  mushrooms, fried zucchini, chiken  0.776563   
50       2               fingers, fried mozzarella or toasted  0.778646   
51       2                                  Mussels di Napeli  0.378646   
52       2                     

## BERT

In [25]:
#df_basic = df_basic_old
model = BertModel.from_pretrained('bert-base-uncased')
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

def texts_to_vectors(texts):
    print("Starting texts_to_vectors function...")
    
    vectors = []
    for cnt, text in enumerate(texts):
        try:            
            inputs = tokenizer([text], return_tensors="pt", truncation=True, padding=True)
            with torch.no_grad():
                outputs = model(**inputs)
            embeddings = outputs.last_hidden_state
            mask = inputs.attention_mask
            masked_embeddings = embeddings * mask.unsqueeze(-1)
            summed = torch.sum(masked_embeddings, 1)
            summed_mask = torch.clamp(mask.sum(1), min=1e-9)
            mean_pooled = summed / summed_mask.unsqueeze(-1)
            vectors.append(mean_pooled[0].numpy())
        except Exception as e:
            print(f"Error encountered while processing text {cnt}: {e}")
            continue
        # Print progress update every 400 samples
        if cnt % 400 == 0:
            percentage = (cnt / len(texts)) * 100
            print(f"Processing text {cnt} of {len(texts)} ({percentage:.2f}% complete)")
    
    print("Finished converting texts to vectors.")
    return np.array(vectors)

vectors = texts_to_vectors(dfs['Text'].tolist())

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.seq_relationship.bias', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.predictions.decoder.weight', 'cls.predictions.transform.dense.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


Starting texts_to_vectors function...
Processing text 0 of 2576 (0.00% complete)
Processing text 400 of 2576 (15.53% complete)
Processing text 800 of 2576 (31.06% complete)
Processing text 1200 of 2576 (46.58% complete)
Processing text 1600 of 2576 (62.11% complete)
Processing text 2000 of 2576 (77.64% complete)
Processing text 2400 of 2576 (93.17% complete)
Finished converting texts to vectors.


In [31]:
df_vectors = pd.DataFrame(vectors, columns=[f'vector_{i}' for i in range(vectors.shape[1])])

# dfs_dropped_text = dfs.drop(columns=['Text'])
dfs_bert = pd.concat([dfs, df_vectors], axis=1)

dfs_bert.to_csv('Combined_menu_23_items_bert.csv',index = False)

In [32]:
dfs_bert.head()

Menu                       Text  center_x  center_y     width    height  \
0     1                      Soups  0.165238  0.062353  0.254286  0.050000   
1     1                         16  0.091905  0.102549  0.063810  0.021373   
2     1          Tom Yum Chicken*.  0.391429  0.104118  0.470476  0.024706   
3     1                       2.95  0.877143  0.106471  0.104286  0.019412   
4     1  spicy & sour w/ mushrooms  0.473810  0.128431  0.540476  0.023529   

       area  uppercase  chars  words  contains_dish  common_words  non_words  \
0  0.012714          1      5      1              0             0          2   
1  0.001364          0      2      1              0             0          0   
2  0.011624          3     17      3              0             3          0   
3  0.002024          0      4      1              0             0          0   
4  0.012717          0     25      5              0             0          1   

   periods  period_btw_numbers  number_end  numbers  commas  exclamation  \
0        0                   0           0        0       0            0   
1        0                   0           1        2       0            0   
2        1                   0           0        0       0            0   
3        1                   1           1        3       0            0   
4        0                   0           0        0       0            0   

   question  colons  underscores  dollar  punctuation  2_periods_cnt  \
0         0       0            0       0            0              0   
1         0       0            0       0            0              0   
2         0       0            0       0            1              0   
3         0       0            0       0            0              0   
4         0       0            0       0            2              0   

   stop_words  prepositions  Item  vector_0  vector_1  vector_2  vector_3  \
0           0             0     0  0.091459  0.064592 -0.371812  0.097875   
1           0             0     0  0.313681  0.307454 -0.021356 -0.150885   
2           0             0     1  0.429004 -0.054322  0.287215 -0.111225   
3           0             0     0  0.041032  0.037430  0.132855 -0.295230   
4           0             0     0  0.105911  0.172013  0.155294  0.086312   

   vector_4  vector_5  vector_6  vector_7  vector_8  vector_9  vector_10  \
0  0.079239 -0.154164  0.180010  0.405308 -0.199024 -0.016061   0.029710   
1 -0.102950 -0.319945  0.285098  0.031769 -0.068357 -0.070376  -0.024982   
2  0.382910  0.091154  0.274636  0.720510 -0.213321 -0.252030   0.007883   
3 -0.157903 -0.491823  0.009724  0.248034  0.284358 -0.272438  -0.304127   
4 -0.012800 -0.087948  0.099761  0.197117  0.058351 -0.022744   0.218358   

   vector_11  vector_12  vector_13  vector_14  vector_15  vector_16  \
0  -0.008122  -0.022195   0.173442  -0.145866  -0.393513   0.129803   
1  -0.229642   0.089192   0.156264  -0.214303   0.104204  -0.195300   
2  -0.231458  -0.149021   0.671505  -0.046596   0.413658   0.107880   
3  -0.128792  -0.112326   0.212748   0.195264   0.404568   0.196831   
4   0.028393   0.119292   0.099116  -0.191342   0.549642   0.190832   

   vector_17  vector_18  vector_19  vector_20  vector_21  vector_22  \
0   0.040539  -0.170086   0.328319   0.189213   0.003754  -0.240214   
1  -0.188596   0.231330   0.135319   0.441800  -0.205802   0.258469   
2   0.033732   0.044343   0.055129   0.232475  -0.428086  -0.415487   
3   0.055021  -0.044944  -0.037675   0.421971   0.192451  -0.070475   
4   0.031604   0.186601   0.602986   0.530319  -0.074371  -0.145434   

   vector_23  vector_24  vector_25  vector_26  vector_27  vector_28  \
0   0.066862   0.077998   0.228630  -0.446388  -0.059167  -0.066074   
1   0.235000   0.337600   0.182496  -0.029245   0.115469  -0.115267   
2  -0.120484   0.408955   0.129628  -0.070130  -0.266398  -0.188089   
3   0.347576   0.305336   0.485185   0.090766  -0.188322  -0.386966   
4   0.197663   0.335254   0.239012

In [22]:
df_labeled = pd.read_csv('Combined_menu_23_items.csv')
dfs.Item = df_labeled.Item
dfs.to_csv('Combined_menu_23_items.csv',index = False)

In [45]:
dfs.to_csv('Combined_menu_10_items.csv')

In [32]:
df = pd.read_csv('Combined_menu_13_items.csv')

In [72]:
df_labeled = pd.read_csv('Combined_menu_23_items.csv')

In [28]:
#df_labeled.drop(columns = ['Unnamed: 0'], inplace = True)

In [29]:
#df_labeled.to_csv('Combined_menu_labeled.csv',index = False)

In [76]:
dfs.to_csv('Combined_menu_23_items.csv',index = False)

In [53]:
# result_df = pd.concat([df_labeled, dfs])

In [27]:
# food_items2 = ["CHEESY MACARONI BITES", "GUAC & CHIPS", "BUFFALO CHICKEN DIP", "WARM PRETZEL BITES", "PEPPERONI FLATBREAD", "QUESO BLANCO & CHIPS", "MARGHERITA FLATBREAD", "CHEESE FRIES", "HARVEST HUMMUS", "TOPGOLF WINGS", "BBQ BRISKET FLATBREAD", "TRES TACOS", "FARMHOUSE FLATBREAD", "SIGNATURE NACHOS", "FRIED CHICKEN SANDWICH", "COBB SALAD", "GRILLED CHICKEN SANDWICH", "FRENCH FRIES", "THE CLASSIC BURGER", "TATER TOTS", "THE SMOKEHOUSE BURGER", "Turkey AVOCADO WRAP", "INJECTABLE DONUT HOLES", "BREAKFAST BURRITO", "CHICKEN BITES", "BRISKET HASH SKILLET", "DOUBLE TROUBLE COOKIE SKILLET", "GRILLED CHEESE", "COOKIE CRUMBLE SUNDAE", "JR CHEESEBURGER", "Bacon & Onion Skillet", "Meat Lover's Skillet", "Popeye's Skillet", "Ham & Mushroom Skillet", "Mexican Skillet", "Western Skillet", "Skirt Steak Skillet", "Veggie Skillet", "Corned Beef Hash Skillet", "Country Skillet", "The Original Benedict", "Idaho Potato Benedict", "Country Benedict", "Benedict Florentine", "CHEESEBURGER LUNCH", "CHILI MAC", "STEAKBURGER LUNCH", "CHILI MAC THREE WAYS", "BOSTON BAKED BEANS", "LETTUCE-TOMATO-BURGER LUNCH", "LETTUCE AND TOMATO SALAD", "CHEESEBURGER", "LETTUCE TOMATO BURGER", "SPECIAL CHOPPED HAM", "SPECIAL HAM AND EGG", "Shrimp Key West", "Parmesan-Crusted Quesadillas", "Zen Chicken Pot Stickers", "Buffalo Wings", "Dragonfire Chicken", "Zen Chicken Pot Stickers", "Friday's Three-For-AII", "Tuscan Spinach Dip", "Breaded Whitefish Sandwich", "Parmesan-Crusted Sicilian Quesadillas", "New England Hot Dog", "Chili Cheese Hot Dog", "Southern Chicken", "Chicken Tenders", "BLT", "ALT", "Veggie Melt"]

In [31]:
# df_new = dfs.copy()
# df_new['Item'] = df_new.Text.isin(food_items2)

# df_new.Item.replace(True,1,inplace = True)
# df_new.Item.replace(False,0,inplace = True)

In [62]:
result_df.to_csv('Combined_menu_23_items.csv', index = False)

In [60]:
result_df.shape

(2576, 16)

In [ ]:
result_df.to_csv('')

In [58]:
result_df.reset_index(drop = True, inplace = True)

In [43]:
df_temp

Menu                                               Text  Item
0        1                                               Eats     0
1        1                                              Bites     0
2        1                                         Shareables     0
3        1                              CHEESY MACARONI BITES     1
4        1                                       GUAC & CHIPS     1
5        1                                BUFFALO CHICKEN DIP     1
6        1              Ranch ad creamy tomato dipping sauces     0
7        1                                                8.5     0
8        1                                         1,300 CAL;     0
9        1                                               10.5     0
10       1                                         1,870 CAL;     0
11       1                                               8.75     0
12       1                                         1,050 CAL.     0
13       1                                 WARM PRETZEL BITES     1
14       1                                PEPPERONI FLATBREAD     1
15       1                               QUESO BLANCO & CHIPS     1
16       1                    Cheese sauce, horseradish Dijon     0
17       1                                              11.25     0
18       1                                           720 CAL.     0
19       1                                                  9     0
20       1                                          1,580 CAL     0
21       1                                                7.5     0
22       1                                           970 CAL.     0
23       1                               MARGHERITA FLATBREAD     1
24       1                                       CHEESE FRIES     1
25       1                                     HARVEST HUMMUS     1
26       1                                               9.75     0
27       1                                         1,580 CAL:     0
28       1                     Roasted carrot hummus, celery;     0
29       1                                              10.75     0
30       1                                           750 CAL.     0
31       1                       carrots cucumber; naan bread     0
32       1                ADD: SMOKED chicken *2.00 [140 CAL)     0
33       1                         ADD: BACON $2.00 (90 CAL.]     0
34       1                                                9.5     0
35       1                                         1,020 CAL,     0
36       1                                      TOPGOLF WINGS     1
37       1                              BBQ BRISKET FLATBREAD     1
38       1  Boneless or bone-in; with carrots, celery; ran...     0
39       1                                         TRES TACOS     1
40       1                                               12.5     0
41       1                                         1,060 CAL,     0
42       1  BUFFALO (10O CAL: ), BBQ (230 CAL: ), ASIAN SE...     0
43       1    Choice of 3 smoked chicken or 3 marinated steak     0
44       1  LEMON PEPPER (130 CAL:] OR GARLIC PARMESAN (38...     0
45       1                   tacos, avocado salsa, lime crema     0
46       1                                     pico de gallo,     0
47       1                                FARMHOUSE FLATBREAD     1
48       1                    BONELESS $11.25, BONE-IN s12.25     0
49       1                                      650-940 CAL ]     0
50       1       cotija cheese, chipotle slaw: corn tortillas     0
51       1            Cauliflower crust; mushrooms, tomatoes_     0
52       1                                         red onion;     0
53       1                                               Trio     0
54       1                                         chicken 10     0
55       1                                  630 CAL, STEAK I1     0
56       1                                                780     0
57       1                                               CAL. 

In [34]:
df_new.to_csv('menu_10_items_labeled.csv',index = False)

In [117]:
import pandas as pd

# Assuming df is your DataFrame and 'column_name' is the name of the column containing the text
df = pd.DataFrame({
    'column_name': ['Petite Maine lobster tails, split and 26', 'Another dish', 'Yet another dish']
})

menu_items = ['lobster tail', 'another menu item', 'yet another menu item']

# Create a new column 'contains_item' that is True if the 'column_name' contains any of the menu items
df['contains_item'] = df['column_name'].apply(lambda x: any(item in x for item in menu_items))

print(df)


                                column_name  contains_item
0  Petite Maine lobster tails, split and 26           True
1                              Another dish          False
2                          Yet another dish          False


In [77]:
# Use pytesseract to get the information about each detected region
data = pytesseract.image_to_data(gray_image, output_type=Output.DICT)

# Prepare an empty dictionary to hold lines of text
lines = {}

# Iterate over each detected region
for i in range(len(data["text"])):
    # Get the information about this region
    x, y, width, height, text = data["left"][i], data["top"][i], data["width"][i], data["height"][i], data["text"][i]

    # Filter out regions that don't contain any text
    if len(text.strip()) == 0:
        continue

    # Group words into lines based on their y-coordinate
    line_key = round(y / height)

    if line_key in lines:
        # Append this word to an existing line
        lines[line_key][0].append(text)
        # Update the font size if this word is larger
        if height > lines[line_key][1]:
            lines[line_key][1] = height
    else:
        # Start a new line with this word
        lines[line_key] = [[text], height]

# Print each line and its font size
for line in lines.values():
    print(f'Font size: {line[1]}, Text: {" ".join(line[0])}')

Font size: 23, Text: BREAKFAST
Font size: 22, Text: Served every and 9am GARCIA’S
Font size: 16, Text: Saturday Sunday from 3pm
Font size: 16, Text: to Enchiladas Suizas
Font size: 14, Text: $12
Font size: 14, Text: ‘Two chicken enchiladas with green tomatillo $12
Font size: 11, Text: large topped
Font size: 22, Text: salsa and served with Mexican beans Vegetarian
Font size: 7, Text: sour
Font size: 21, Text: cream, rice, $12 Red Menudo Chilaquiles
Font size: 18, Text: and SOUTH BORDER bowl
Font size: 16, Text: eggs. Mexican Omelette
Font size: 31, Text: Huevos Rancheros your
Font size: 28, Text: A tortilla tower, refried ranchera, Omelette flour tortillas. protein Breakfast
Font size: 9, Text: crispy easy eggs
Font size: 28, Text: beans, topped CANTINA & GRILL our version
Font size: 16, Text: rice over Burrito
Font size: 16, Text: with salsa melted cheese crowned with $11 Divorciados $11)
Font size: 15, Text: sour cream queso $12 combination of red served with spicy peppers, $10
Font 

In [46]:
pd.concat([pd.read_csv('menu_2p2.csv'),pd.read_csv('olive-garden-menu-2.csv'),pd.read_csv('olive-garden-menu-6.csv')\
          ,pd.read_csv('Red-Lobster-menu-1.csv'),pd.read_csv('Red-Lobster-menu-2.csv')\
           ,pd.read_csv('Red-Lobster-menu-5.csv')], ignore_index=True)

Unnamed: 0  Menu                                       Text  Char_Count  \
0             0     1                            tom yum chicken          15   
1             1     1                     spicy sourwmushrooms l          22   
2             2     1                       in lemon grass broth          20   
3             3     1                       tom yum goong shrimp          20   
4             4     1                                          l           1   
5             5     1                        tom kha kai chicken          19   
6             6     1                     creamy coconut milk, l          22   
7             7     1                lemon grass, straw mushroom          27   
8             8     1                                    galanga           7   
9             9     1                   soft tofu soup ccccsss d          24   
10           10     1                         ground pork bean l          18   
11           11     1                thread noodles w vegetables          27   
12           12     1                               noodle soups          12   
13           13     1                           rice noodle soup          16   
14           14     1         rice noodle w bean sprouts, choice          34   
15           15     1                  of chicken, beef, or pork          25   
16           16     1                               bamee wonton          12   
17           17     1                 egg noodle or wonton w bbq          26   
18           18     1            pork, bean sprouts, green onion          31   
19           19     1                                   cilantro           8   
20           20     1                             tom yum noodle          14   
21           21     1                spicy rice or egg noodles w          27   
22           22     1            ground pork, bean sprouts, fish          31   
23           23     1                      balls crushed peanuts          21   
24           24     1                 red or gree cccceccseceees          26   
25           25     1                               curry noodle          12   
26            0     2                                      ander           5   
27            1     2                       antipasti appetizers          20   
28            2     2                  create a sampler italiano          25   
29            3     2       stufes mushrooms prepared with clams          36   
30            4     2                w three choices two choices          27   
31            5     2  calamari stuffed mushrooms fried zucchini          41   
32            6     2           chicken fingers fried mozzarella          32   
33            7     2                 toasted best and pork rave          26   
34            8     2                                 bruschetta          10   
35            9     2                          caprese flatbread          17   
36           10     2                  grilled chicken flatbread          25   
37           11     2                          mussels di napoli          17   
38           12     2                   hot artichokespinach dip          24   
39           13     2                              lasagna frita          13   
40           14     2                  smoked mozzarella fonduta          25   
41           15     2             dipping sauces for breadsticks          30   
42           16     2             j alfredo sauce marinara sauce          30   
43           17     2                            sicilian scampi          15   
44           18     2                          stuffed mushrooms          17   
45           19     2                                   calamari           8   
46           20     2              zuppe e insalate soups salads          29   
47           21     2                            chicken gnocchi          15   
48           22     2                             pasta e fagiol          14   
49   

- Menu 1: Asian menu, "menu_2p2"
- Menu 2: Olive Garden, "olive-garden-menu-6"
- Menu 3: Red Lobster, "Red-Lobster-menu-1"
- Menu 4: Red Lobster, "Red-Lobster-menu-2"
- Menu 5: Red Lobster, "Red-Lobster-menu-5"
- Menu 6: Mexican menu,'mexican-menu-1'
- Menu 7: Mexican menu, 'mexican-menu-2'
- Menu 8: Mexican menu,'mexican-menu-3',
- Menu 9: Mexican menu,'mexican-menu-4',
- Menu 10: American menu,'american-menu-1',
- Menu 11: American menu,'american-menu-2'
- Menu 12: Random menu,'ivy-menu-1'
- Menu 13: Random menu,'ivy-menu-2'
- Menu 14: Top Golf, 'topgolf_menu'
- Menu 15: Eggcited, 'eggcited_menu'
- Menu 15: Steak & Shake, 'steak-n-shake'
- Menu 17: TGI Friday's, 'tgi_menu'
- Menu 18: Portillos, 'portillos_menu'
- Menu 19: Portillos, 'portillos_menu2'
- Menu 20: Meatheads, 'meatheads_menu'
- Menu 21: Meatheads, 'meatheads_menu2'
- Menu 22: PitaPit, 'PitaPit_menu'
- Menu 23: PitaPit, 'PitaPit_menu2'

Make another feature indicating the type of cuisine? This might be something the user would input to help the model make more accurate classification. 

In [58]:
df_cars = pd.read_csv('/Users/alex/Data_Science/Used_Cars/Car_Price_Prediction/car_data_sorted_Full.csv')

In [63]:
df_cars[(2010 > df_cars.Year) & (df_cars.Year > 2000)].Color.value_counts()

White     2769
Silver    2087
Black     2064
Grey      1590
Blue      1244
Red        906
Green      397
Brown      323
Custom     212
Yellow     100
Orange      56
Purple      46
Name: Color, dtype: int64

In [6]:
df = pd.read_csv('Combined_menu_13_items.csv')

In [11]:
df.drop(columns = ['Unnamed: 0'],inplace = True)

KeyError: "['Unnamed: 0'] not found in axis"

In [19]:
df.Text.values.tolist()

['Soups',
 '16',
 'Tom Yum Chicken*.',
 '2.95',
 'spicy & sour w/ mushrooms',
 'L5.95',
 'in lemon grass broth',
 '17',
 'Tom Yum Goong (shrimp) ,3.95',
 'L6.95',
 '18',
 'Tom Kha Kai (chicken)',
 '2.95',
 'creamy coconut milk;',
 'L5.95',
 'lemon grass, straw mushroom',
 '& galanga',
 '19',
 'Soft Tofu Soup',
 '2.95',
 'ground pork & bean',
 'L5.95',
 'thread noodles w/ vegetables',
 'Noodle Soups',
 '20',
 'Rice Noodle Soup',
 '6.95',
 'rice noodle w/ bean sprouts, choice]',
 'of chicken, beef,or pork',
 '21',
 'Bamee/ Wonton',
 '6.95',
 'egg noodle or wonton w/ BBQ',
 'pork,bean sprouts, green onion',
 '& cilantro',
 '22',
 'Tom Yum Noodle*_',
 '7.25',
 'spicy rice or egg noodles w/',
 'groundpork; bean sprouts,fish',
 'balls & crushedpeanuts',
 '23',
 'Red or Green',
 '7.95',
 'Curry Noodle*',
 'Ogander/',
 'Create a Samplet Italiane',
 'Antipasti',
 'Choose from: caramel, stuffed',
 'mushrooms, fried zucchini, chiken',
 'fingers, fried mozzarella or toasted',
 'Mussels di Napeli',

In [20]:
pd.options.display.max_rows = 5000

In [20]:
df_new = df.copy()

In [21]:
food_items = ['Tom Yum Chicken*.', 'Soft Tofu Soup', 'Noodle Soups', 'Rice Noodle Soup', 'Bamee/ Wonton', 'Tom Yum Noodle*_', 'Curry Noodle*', 'Hot Articheke-Spinach', 'Captese Flatbread', 'Grilled Chiken Flatbread', 'Ultimate Feast"', 'Mixed Grill*', 'Fresh Atlantic', 'Bar Harbor Lobster Bake', 'Seaside Shrimp Trio', 'Parrot Isle Jumbo', 'Garlic Shrimp', 'Coconut Shrimp', 'Wood-Grilled Tilapia', 'Shrimp Linguini', 'Sea Scallops', 'Soy-Ginger Salmon*', 'Dragon Shrimp', 'Southwest-Style Tacos', 'Salmon New Orleans*', 'Grilled Shrimp', 'Grilled Chicken', 'Grilled Tilapia', 'Lobster Meat', 'Wild-Caught Snow Crab Legs', 'Shrimp Linguini Alfredo', 'Parrot Isle Jumbo Coconut', 'Crab Linguini Alfredo', 'Signature Creamy Lobster', 'Wood-Grilled Shrimp', 'Shrimp Your', 'Rock Lobster Tail', 'Live Maine Lobster', 'Mlou Sokstex?', 'Seafood-Stuffed Mushrooms', 'Langostino Lobster-Artichoke-', 'Signature Jumbo Shrimp', 'Peppercorn-Panko Calamari', 'Seaside Sampler', 'Seafood-Stuffed Mushrooms', 'Parrot Isle Jumbo Coconut Shrimp', 'Sweet Chili Shrimp', 'Create Your Own Appetizer', 'Mozzarella Cheesesticks', 'Mozzarella Cheesesticks', 'Chicken Breast Strips', 'Parrot Isle Jumbo Coconut', 'Clam Strips', 'Seafood-Stuffed Mushrooms', 'Roasted-Garlic Mussels', 'New England Clam Chowder', 'Classic Caesar Salad', 'Lobster Bisque', 'Creamy Potato Bacon', 'Wood-Grilled Shrimp', 'Wood-Grilled Fresh Salmon*', 'Wood-Grilled Chicken', 'Enchiladas Suizas $12', 'Huevos Rancheros $12', 'Mexican Omelette S12', 'Breakfast Burrito $10', 'Brunch Drinks', 'Machaca & Eggs S12', 'Draft Beer S5', 'Micheladas $6', 'Mexican Coffee $6', 'Carne Asada Breakfats $14', 'Chicken En', 'Salad $14', 'Mexican Cobb" Salad $13', 'With Shrimp 517', 'Blackened Sea Bass Salad $16', 'Mahi Mahi Burrito $16', 'Shrimp Enchiladas $16', 'Signature Fish Taco Platter $16', 'Ahi Tacos $16', 'Blackened Salmon Filet $19', 'Enchiladas Espanolas $15', 'Signature Mole Enchiladas $15', 'Classic Combination $14', 'Chile Relleno $13', 'Enchiladas Suizas $14', 'Grilled Chicken Diablo $15', 'Chilaquiles $14', 'Taquitos $12', 'Chipotle Chicken Avocado Torta $12', 'Three Flautas $13', 'Grilled Shrimp Fajita Burrito $15', 'Carnitas S15', 'Original Carne Asada $18', 'Chile Colorado S15', 'De Ia Olla Beans_', 'Olla Beans:', 'Chile Verde $15', 'Vegetable Fajitas 515', 'Fajitas $16', 'Mevican Pastries', 'Traditional Flan $6', 'Bunuelos $6', 'Fried Ice Cream $7', 'Two Tacos', 'Chicken Fingers', 'Soft Drinks', 'Iced Tea', 'Baby Cilantro', 'Garlic Parmesan Flour, Lemon Gremolata, Cocktail Sauce', 'B A R', 'Baby Spinach, Parmesan, Swiss Cheese', 'Wild Pacific Brown Shrimp', 'Candied Walnuts, Raisin Crostini', 'Imported Buffalo Mozzarella, San Marzano Tomatoes, Basil,', 'All Five', 'Extra Virgin Olive Oil', 'Harissa Mayonnaise', 'Arugula Prosciutto, Sliced Grape Tomatoes,', 'Imported Buffalo Mozzarella, Gran Cru Cheese', 'Charcoal Grilled Garlic Crostini, Extra Virgin Olive Oil,', 'Mortadella, Pistachios, Roasted Cauliflower,', 'Laura Chenel Goat Cheese', 'Brussels Sprouts, Fontina', 'Roasted Garlic, Wild Mushrooms, Imported Buffalo', 'Citrus Sesame Dressing', 'Braised Leeks, Tomato, Tarragon', 'Appropriately Garnished', 'Italian Style Custard, Salted Caramel,', 'Chocolate Cookie Crumbles', 'Candied Walnuts, Raisin Crostini', 'All Five', 'Mocha Mousse, Sea Salt Caramel Gelato', 'Vanilla Bean Sauce, Strawberry Gelato', 'Applewood Smoked Bacon, Blue Cheese, Scallion,', 'Seasonal Apples, Angelo Gelato Spiced Pumpkin', 'The Real Deall', 'Daily Produce, Sun-Dried Tomatoes, Whipped Potatoes,', 'Pan Seared Salmon, Mango, Avocado, Scallion,', 'Applewood Smoked Bacon, Tomato, Scallion, Red Onion,', 'Applewood Smoked Bacon, Roasted Cor, Egg. Avocado,', 'Queso Fresco,Tomatillo Salsa, Jicama-Cabbage Slaw,', 'Lime Cream, Flour Tortillas', 'Mascarpone, Fresh Herbs,', 'Bleu Cheese, Mixed Greens, Sauteed Apples,', 'Parmigiano-Reggiano, Baby Sweet Potato Chips', 'Candied Walnuts, Apple Cider Vinaigrette', 'Shrimp; Spanish Chorizo, Mussels, Finfish, Saffron', 'Basmati Rice, Peas', 'Applewood Smoked Bacon, Tomatoes, Onions,', 'Haricot Verts, Avocado, Sweet & Spicy Vinaigrette', 'Add Grilled Chicken Breast _', 'Add Charcoal Grilled Gulf Shrimp', 'Add Crispy Foley Calamari_', 'Add Charcoal Grilled Faroe Island Salmon', 'Whipped Potatoes, Charred Lemon, Sauteed Garlic Spinach', 'Crispy Onions', 'Smoked Gouda, Applewood Smoked Bacon, Cavatappi', 'Sweet Potato Fries,', 'Moody Blue Cheese, Crispy Onions, Lettuce, Tomato,', 'Apple-Cider Grain Mustard Glaze', 'Chipotle Mayonnaise , Toasted Buttered Challah Bun', 'Monterey Jack, Applewood Smoked Bacon, Lettuce,', 'Heirloom Canrot Salad, Caramelized Cippolini Onions, Sauteed', 'Fresh Mint', 'Tomato, Red Onion, Honey Mustard Sauce, Stirato Roll', 'Sugar Snap Peas, Asparagus Veloute', 'Julienne Vegetables, Kalbi Sauce, Steamed Baby', 'Applewood Smoked Bacon, Lettuce, Tomato, Mayonnaise,', 'Fingerling Potato, Yellow Tomato Broth, Citrus, Radish,', 'Bok Choy, Spicy Miso Glaze, Fried Lotus Root', 'Toasted Nine Grain Bread', 'Shaved Fennel, Frisee', 'Mascarpone, Fresh Herbs, Parmigiano-Reggiano', 'Medley Pepperjack Cheese,', 'Drawn Butter', 'Lettuce, Tomato, Buttered Griddled Challah Bun', 'Whipped Potatoes, Seasonal Vegetable, Red Wine Reduction', 'Moody Blue Cheese, Crispy Onions, Lettuce, Tomato,', 'Chipotle Mayonnaise, Toasted Buttered Challah Bun', 'Jonah Crab; Scallops Calamari, Manila Clams, Mussels,', 'Guacamole, Lettuce, Tomato, Ranch Dressing, Spinach Tortilla', 'Red Wine Reduction', 'Chopped Pecans: Water Chestnuts, Celery,', 'Butter Griddled Sourdough Bread', 'Moody Blue Cheese, Crispy Onions,Chipotle', 'Mayonnaise, Toasted Buttered Challah Bun, Pickle,', 'Lump Blue Crab, Remoulade Sauce, Grilled Challah Bun']

In [22]:
df_new['Item'] = df_new.Text.isin(food_items)

In [26]:
df_new[['Text','Item']]

Text  Item
0                                                 Soups     0
1                                                    16     0
2                                     Tom Yum Chicken*.     1
3                                                  2.95     0
4                             spicy & sour w/ mushrooms     0
5                                                 L5.95     0
6                                  in lemon grass broth     0
7                                                    17     0
8                          Tom Yum Goong (shrimp) ,3.95     0
9                                                 L6.95     0
10                                                   18     0
11                                Tom Kha Kai (chicken)     0
12                                                 2.95     0
13                                 creamy coconut milk;     0
14                                                L5.95     0
15                          lemon grass, straw mushroom     0
16                                            & galanga     0
17                                                   19     0
18                                       Soft Tofu Soup     1
19                                                 2.95     0
20                                   ground pork & bean     0
21                                                L5.95     0
22                         thread noodles w/ vegetables     0
23                                         Noodle Soups     1
24                                                   20     0
25                                     Rice Noodle Soup     1
26                                                 6.95     0
27                 rice noodle w/ bean sprouts, choice]     0
28                             of chicken, beef,or pork     0
29                                                   21     0
30                                        Bamee/ Wonton     1
31                                                 6.95     0
32                          egg noodle or wonton w/ BBQ     0
33                       pork,bean sprouts, green onion     0
34                                           & cilantro     0
35                                                   22     0
36                                     Tom Yum Noodle*_     1
37                                                 7.25     0
38                         spicy rice or egg noodles w/     0
39                        groundpork; bean sprouts,fish     0
40                               balls & crushedpeanuts     0
41                                                   23     0
42                                         Red or Green     0
43                                                 7.95     0
44                                        Curry Noodle*     1
45                                             Ogander/     0
46                            Create a Samplet Italiane     0
47                                            Antipasti     0
48                        Choose from: caramel, stuffed     0
49                    mushrooms, fried zucchini, chiken     0
50                 fingers, fried mozzarella or toasted     0
51                                    Mussels di Napeli     0
52                               beef and pork ravioli.     0
53                  Mussels in the shell, simmered with     0
54               Stuffed mushrooms prepared with clams.     0
55                       wine, garlic butter and unions     0
56                                  Three Choices 11.50     0
57                                                10.75     0
58                                    Two Choices 10.25     0
59                                Hot Articheke-Spinach     1
60                                    Captese Flatbread     1
61                   A blend of artichokes, spinach and     0
62                      Mozzarella cheese. tomatoes and     0
63              cream cheese, Served with Tuscan bread:     0
64                   

In [25]:
df_new.Item.replace(True,1,inplace = True)
df_new.Item.replace(False,0,inplace = True)

In [31]:
df_labeled.columns.tolist()

['Unnamed: 0',
 'Menu',
 'Text',
 'Height',
 'Uppercase_Count',
 'Char_Count',
 'Word_Count',
 'Common_Words',
 'other_words',
 'commas',
 'colons',
 'dollar',
 'Item']

In [ ]:
df_labeled.Item

In [35]:
df_labeled[['Menu','Text','Height','Common_Words','Item']]

Menu                                               Text  Height  \
0        1                                              Soups     255   
1        1                                                 16     109   
2        1                                  Tom Yum Chicken*.     126   
3        1                                               2.95      99   
4        1                          spicy & sour w/ mushrooms     120   
5        1                                              L5.95     100   
6        1                               in lemon grass broth     128   
7        1                                                 17     104   
8        1                       Tom Yum Goong (shrimp) ,3.95     156   
9        1                                              L6.95      99   
10       1                                                 18     110   
11       1                              Tom Kha Kai (chicken)     134   
12       1                                               2.95     104   
13       1                               creamy coconut milk;     125   
14       1                                              L5.95     110   
15       1                        lemon grass, straw mushroom     126   
16       1                                          & galanga     133   
17       1                                                 19     110   
18       1                                     Soft Tofu Soup     149   
19       1                                               2.95     104   
20       1                                 ground pork & bean     137   
21       1                                              L5.95     108   
22       1                       thread noodles w/ vegetables     138   
23       1                                       Noodle Soups     245   
24       1                                                 20     120   
25       1                                   Rice Noodle Soup     162   
26       1                                               6.95     110   
27       1               rice noodle w/ bean sprouts, choice]     145   
28       1                           of chicken, beef,or pork     163   
29       1                                                 21     113   
30       1                                      Bamee/ Wonton     137   
31       1                                               6.95     109   
32       1                        egg noodle or wonton w/ BBQ     140   
33       1                     pork,bean sprouts, green onion     157   
34       1                                         & cilantro     114   
35       1                                                 22     117   
36       1                                   Tom Yum Noodle*_     133   
37       1                                               7.25     109   
38       1                       spicy rice or egg noodles w/     148   
39       1                      groundpork; bean sprouts,fish     149   
40       1                             balls & crushedpeanuts     149   
41       1                                                 23     120   
42       1                                       Red or Green     136   
43       1                                               7.95     117   
44       1                                      Curry Noodle*     147   
45       2                                           Ogander/     266   
46       2                          Create a Samplet Italiane      57   
47       2                                          Antipasti     147   
48       2                      Choose from: caramel, stuffed      42   
49       2                  mushrooms, fried zucchini, chiken      42   
50       2               fingers, fried mozzarella or toasted      45   
51       2                                  Mussels di Napeli      54   
52       2                             beef and pork ravioli.      45   
53       2                Mussels in the shell, simmered with   

In [6]:
# #from autocorrect import Speller
# non_words = ["with", "choice","add","oz","available","w",'served','side']
# file_name = "mexican-menu-1.jpeg"
# name = file_name.split(".")[0]
# # Load the image from a file
# image = cv2.imread(file_name)

# # Convert the image to gray scale
# gray_image = cv2.cvtColor(image, cv2.COLOR_BGR2GRAY)

# # Run pytesseract on the gray scale image
# text = pytesseract.image_to_string(gray_image)

# # Split the text into lines
# lines = text.split('\n')

# # Remove non-alphabetical, non-numerical characters and non-periods from each line
# lines = [re.sub(r'[^a-zA-Z , $ : ]', '', line) for line in lines]

# # Replace multiple spaces with a single space
# lines = [re.sub(' +', ' ', line) for line in lines]

# # Create a dataframe with each line as a separate item
# df = pd.DataFrame(lines, columns=['Text'])

# # Strip leading and trailing whitespaces from the 'Text' column
# df.insert(0, 'Menu', 6)
# df['Text'] = df['Text'].str.strip()

# # Remove empty rows
# df = df[df['Text'].str.strip() != '']
# df['Text'] = df['Text'].str.lower()

# df.reset_index(drop = True,inplace = True)

# # Add character count
# df['Char_Count'] = df['Text'].apply(len)

# # Add word count
# df['Word_Count'] = df['Text'].apply(lambda x: len(x.split()))

# df['Common_Words'] = df['Text'].apply(lambda x: sum(word in common_menu_words for word in x.split()))

# df['other_words'] = df['Text'].apply(lambda x: sum(word in non_words for word in x.split()))

# df['commas'] = df['Text'].apply(lambda x: x.count(','))
# df['colons'] = df['Text'].apply(lambda x: x.count(':'))
# df['dollar'] = df['Text'].apply(lambda x: x.count('$'))

# df['Item'] = np.zeros(len(df))
# df['Item'] = df['Item'].astype('int')

# # Get OCR output using pytesseract
# d = pytesseract.image_to_string(image, output_type=Output.DICT)

# # Get number of lines
# n_boxes = len(d['level'])

# # Create a DataFrame to store line text and size
# df = pd.DataFrame()

# for i in range(n_boxes):
#     (text, x, y, w, h) = (d['text'][i], d['left'][i], d['top'][i], d['width'][i], d['height'][i])
    
#     # Only include boxes with a w/h ratio greater than 3, this helps eliminate noise from OCR
#     if w/h > 3:
#         df = df.append({'Text': text, 'Size': h}, ignore_index=True)

# df.to_csv(name +'.csv')

KeyError: 'level'

In [4]:
# popular_menu_items = [
#     "Cheeseburger", "Pepperoni Pizza", "Fried Chicken", "Spaghetti Bolognese", "Chicken Alfredo", 
#     "Caesar Salad", "Chicken Caesar Wrap", "Chicken Parmesan", "Chicken Tikka Masala", "Beef Tacos",
#     "Margherita Pizza", "Chicken Fried Rice", "Chicken Teriyaki", "Chicken Pad Thai", 
#     "Chicken Shawarma", "Chicken Souvlaki", "Chicken Enchiladas","Beef Souvlaki", 
#     "Beef Pad Thai", "Beef Teriyaki", "Beef Fried Rice",
#     "Shrimp Tacos", "Shrimp Fried Rice", "Shrimp Teriyaki", "Shrimp Pad Thai", 
#     "Shrimp Shawarma", "Shrimp Souvlaki", "Shrimp Enchiladas", "Shrimp Burrito",
#     "Lobster Roll", "Lobster Bisque", "Lobster Thermidor", "Lobster Newburg", "Lobster Fra Diavolo", 
#     "Lobster Mac and Cheese", "Lobster Ravioli", "Lobster Paella", "Lobster Risotto", "Lobster Linguini",
#     "Crab Cakes", "Crab Rangoon", "Crab Bisque", "Crab Louie", "Crab Stuffed Mushrooms", 
#     "Crab Linguini", "Crab Risotto", "Crab Paella", "Crab Ravioli", "Crab Mac and Cheese",
#     "Clam Chowder", "Clam Linguini", "Clam Risotto", "Clam Paella", "Clam Ravioli", 
#     "Clam Mac and Cheese", "Clam Stuffed Mushrooms", "Clam Louie", "Clam Bisque", "Clam Rangoon",
#     "Oyster Po' Boy", "Oyster Rockefeller", "Oyster Stew", "Oyster Linguini", "Oyster Risotto", 
#     "Oyster Paella", "Oyster Ravioli", "Oyster Mac and Cheese", "Oyster Stuffed Mushrooms", "Oyster Louie",
#     "Fish and Chips", "Fish Tacos", "Fish Chowder", "Fish Linguini", "Fish Risotto", 
#     "Fish Paella", "Fish Ravioli", "Fish Mac and Cheese", "Fish Stuffed Mushrooms", "Fish Louie",
#     "Eggplant Parmesan", "Eggplant Lasagna", "Eggplant Rollatini", "Eggplant Caponata", "Eggplant Moussaka", 
#     "Eggplant Ratatouille", "Eggplant Baba Ghanoush", "Eggplant Shakshuka", "Eggplant Curry", "Eggplant Stir Fry"
# ]